In [62]:
import torch
from torch.utils.data import Dataset
class AudioDataset(Dataset):
    def __init__(self, features, labels=None):
        self.features = features
        self.labels = labels

    def __len__(self):
        return len(self.features)

    def __getitem__(self, idx):
        if self.labels is not None:
            return self.features[idx], self.labels[idx]
        return self.features[idx]


In [63]:
import torch
import torch.nn as nn
from pymongo import MongoClient
import numpy as np
from sklearn.preprocessing import StandardScaler
from torch.utils.data import Dataset, DataLoader

# Define your ANN model
class ANN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(ANN, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, 1)
        self.relu = nn.ReLU()

    def forward(self, x):
        # Handling both single samples and batches
        if len(x.shape) == 1:
            x = x.unsqueeze(0)
        x = self.fc1(x)
        x = self.relu(x)
        x = self.fc2(x)
        return x.squeeze()


# Define your dataset
# Define your dataset
class AudioDataset(Dataset):
    def __init__(self, cursor):
        self.cursor = cursor
        self.scaler = StandardScaler()
        self.features = []

        # Iterate through documents and extract features
        for doc in self.cursor:
            if 'features' in doc and 'mfccs_stats' in doc['features']:
                mfccs_mean = np.array(doc['features']['mfccs_stats']['mean'])

                # Reshape mfccs_mean to have a fixed size (1, 20)
                mfccs_mean = mfccs_mean[:20]  # Trim or pad as necessary
                mfccs_mean = np.pad(mfccs_mean, (0, 20 - len(mfccs_mean)), mode='constant')  # Pad if less than 20
                song_features = mfccs_mean

                self.features.append(song_features)

        # Standardize features
        self.features = np.array(self.features)
        print("Shape of self.features before scaling:", self.features.shape)

        self.features = self.scaler.fit_transform(self.features)

    def __len__(self):
        return len(self.features)

    def __getitem__(self, idx):
        return {
            'features': torch.from_numpy(self.features[idx]).float().unsqueeze(0)  # Reshape to (1, 20)
        }


# Setup MongoDB connection
client = MongoClient('mongodb://localhost:27017/')
db = client['Dataset']
collection = db['audio']

# Fetch documents
documents = collection.find({}).limit(119415)  # Limiting to 500,000 entries

# Initialize Dataset and DataLoader
dataset = AudioDataset(documents)
dataloader = DataLoader(dataset, batch_size=64, shuffle=True)

# Define model, optimizer, and loss function
model = ANN(input_size=dataset.features.shape[1], hidden_size=64)
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
criterion = nn.MSELoss()

# Training loop
for epoch in range(100):
    for batch in dataloader:
        features = batch['features']

        optimizer.zero_grad()
        outputs = model(features)
        loss = criterion(outputs, torch.zeros_like(outputs))  # Modify target according to your task
        loss.backward()
        optimizer.step()

    print(f'Epoch {epoch + 1}, Loss: {loss.item()}')

# Now you can use the trained model for music recommendation
# Save the trained model
torch.save(model.state_dict(), "model.pth")


Shape of self.features before scaling: (26589, 20)
Epoch 1, Loss: 0.00046112498966977
Epoch 2, Loss: 0.00010888899123528972
Epoch 3, Loss: 5.5427350162062794e-05
Epoch 4, Loss: 2.4151126126525924e-05
Epoch 5, Loss: 1.3985305486130528e-05
Epoch 6, Loss: 7.914261004771106e-06
Epoch 7, Loss: 2.275371798532433e-06
Epoch 8, Loss: 2.765511624147621e-07
Epoch 9, Loss: 1.1430613966467718e-07
Epoch 10, Loss: 6.189713630533333e-09
Epoch 11, Loss: 2.8577857857925437e-09
Epoch 12, Loss: 7.855447542448601e-11
Epoch 13, Loss: 1.3648599394774918e-12
Epoch 14, Loss: 6.867234103417885e-13
Epoch 15, Loss: 4.1974775299427267e-14
Epoch 16, Loss: 3.092492761425092e-06
Epoch 17, Loss: 2.208108695889166e-10
Epoch 18, Loss: 4.009066134624817e-10
Epoch 19, Loss: 1.494354592068703e-06
Epoch 20, Loss: 3.781603474806161e-09
Epoch 21, Loss: 5.184699241114754e-13
Epoch 22, Loss: 2.687661482259074e-10
Epoch 23, Loss: 3.0193876909834216e-07
Epoch 24, Loss: 1.544203200865013e-07
Epoch 25, Loss: 1.577343533565312e-10
E

In [64]:
from sklearn.model_selection import KFold

# Define your training parameters
num_epochs = 100
kf = KFold(n_splits=5, shuffle=True)  # 5-fold cross-validation

# List to store validation losses for each fold
validation_losses = []

# Perform cross-validation
for fold, (train_indices, val_indices) in enumerate(kf.split(dataset)):
    print(f"Fold {fold + 1}:")

    # Split the dataset into training and validation sets
    train_dataset = torch.utils.data.Subset(dataset, train_indices)
    val_dataset = torch.utils.data.Subset(dataset, val_indices)
    
    train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
    val_loader = DataLoader(val_dataset, batch_size=64, shuffle=False)
    
    # Initialize model, optimizer, and loss function
    model = ANN(input_size=dataset.features.shape[1], hidden_size=64)
    optimizer = optim.Adam(model.parameters(), lr=0.001)
    criterion = nn.MSELoss()
    
    # Training loop
    for epoch in range(num_epochs):
        for batch in train_loader:
            features = batch['features']
            
            optimizer.zero_grad()
            outputs = model(features)
            loss = criterion(outputs, torch.zeros_like(outputs))  # Modify target according to your task
            loss.backward()
            optimizer.step()

    # Evaluate the model on the validation set
    val_losses = []
    for batch in val_loader:
        features = batch['features']
        outputs = model(features)
        loss = criterion(outputs, torch.zeros_like(outputs))  # Modify target according to your task
        val_losses.append(loss.item())
    
    # Calculate average validation loss for this fold
    avg_val_loss = np.mean(val_losses)
    validation_losses.append(avg_val_loss)
    print(f"Validation Loss: {avg_val_loss}")

# Calculate average validation loss across all folds
avg_validation_loss = np.mean(validation_losses)
print(f"Average Validation Loss: {avg_validation_loss}")


Fold 1:
Validation Loss: 3.290783716953476e-09
Fold 2:
Validation Loss: 3.432304517901277e-10
Fold 3:
Validation Loss: 2.5773767643931323e-09
Fold 4:
Validation Loss: 6.141048345356639e-10
Fold 5:
Validation Loss: 2.2120120486594772e-10
Average Validation Loss: 1.4093393945076694e-09


In [65]:
# Training loop
for epoch in range(num_epochs):
    print(f"Epoch {epoch + 1}:")
    for batch_idx, batch in enumerate(train_loader):
        features = batch['features']
        
        optimizer.zero_grad()
        outputs = model(features)
        loss = criterion(outputs, torch.zeros_like(outputs))  # Modify target according to your task
        loss.backward()
        optimizer.step()
        
        print(f"\tBatch {batch_idx + 1}/{len(train_loader)} - Loss: {loss.item()}")


Epoch 1:
	Batch 1/333 - Loss: 2.9578826909494593e-13
	Batch 2/333 - Loss: 1.224957461853915e-11
	Batch 3/333 - Loss: 5.30507512919165e-11
	Batch 4/333 - Loss: 9.837414910451869e-11
	Batch 5/333 - Loss: 1.5307251299834235e-10
	Batch 6/333 - Loss: 2.0574451864430188e-10
	Batch 7/333 - Loss: 2.5047722229665226e-10
	Batch 8/333 - Loss: 2.783923647164954e-10
	Batch 9/333 - Loss: 2.8815050345798454e-10
	Batch 10/333 - Loss: 2.8104493732250546e-10
	Batch 11/333 - Loss: 2.564347345579421e-10
	Batch 12/333 - Loss: 1.906628049885839e-10
	Batch 13/333 - Loss: 1.2085731027067226e-10
	Batch 14/333 - Loss: 6.586854672807618e-11
	Batch 15/333 - Loss: 2.857211342521815e-11
	Batch 16/333 - Loss: 7.526412652836267e-12
	Batch 17/333 - Loss: 1.2448601990813074e-13
	Batch 18/333 - Loss: 1.3335664170166517e-11
	Batch 19/333 - Loss: 2.6251559953616166e-11
	Batch 20/333 - Loss: 9.472002349131259e-11
	Batch 21/333 - Loss: 2.0114092336154243e-10
	Batch 22/333 - Loss: 3.6744762788032403e-10
	Batch 23/333 - Loss:

In [68]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import numpy as np
from pymongo import MongoClient
from sklearn.preprocessing import StandardScaler

# Correct the class definition
class ANN(nn.Module):
    def __init__(self, input_size, hidden_size):  # Correct use of double underscores
        super(ANN, self).__init__()  # Correct use of double underscores for superclass initializer
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, 1)
        self.relu = nn.ReLU()
       
    def forward(self, x):
        x = self.fc1(x)
        x = self.relu(x)
        x = self.fc2(x)
        return x

# Function to load the model
def load_model(model_path, input_size, hidden_size):
    model = ANN(input_size, hidden_size)
    model.load_state_dict(torch.load(model_path))
    model.eval()
    return model

# Example usage
client = MongoClient('mongodb://localhost:27017/')
db = client['Dataset']
collection = db['audio']
model = load_model('model.pth', input_size=20, hidden_size=64)

# Assuming the rest of your function to fetch and process data is correct,
# your model is now correctly defined and can be used as intended.

In [75]:
import torch
from pymongo import MongoClient
from sklearn.preprocessing import StandardScaler
import numpy as np

def fetch_features(db, song_id=None, filename=None):
    """ Fetch features for a specific song by ID or filename from MongoDB. """
    query = {"_id": song_id} if song_id else {"filename": filename}
    song_data = db.audio.find_one(query)
    if not song_data:
        return None

    mfccs = np.array(song_data['features']['mfccs_stats']['mean'])
    features = np.reshape(mfccs, (1, -1))  # Reshape for single sample
    return features

def find_similar_songs(model, db, input_features, num_results=5):
    """ Find songs similar to the provided features using the trained model. """
    scaler = StandardScaler()

    # Process input features
    input_features = scaler.fit_transform(input_features)
    input_vector = torch.tensor(input_features, dtype=torch.float32)
    input_vector = model(input_vector).detach().numpy()

    # Fetch all songs features
    all_songs = db.audio.find()
    all_features = []
    song_ids = []

    for song in all_songs:
        if 'features' in song and 'mfccs_stats' in song['features']:
            mfccs = np.array(song['features']['mfccs_stats']['mean'])
            all_features.append(mfccs)
            song_ids.append(song['_id'])
        else:
            print(f"Skipping song {song['_id']} because it doesn't have mfccs_stats")

    all_features = np.array(all_features)

    all_features = scaler.transform(all_features)
    all_features_tensor = torch.tensor(all_features, dtype=torch.float32)
    all_vectors = model(all_features_tensor).detach().numpy()

    # Calculate distances and find the most similar songs
    distances = np.linalg.norm(all_vectors - input_vector, axis=1)
    nearest_indices = np.argsort(distances)[:num_results]
    return [song_ids[i] for i in nearest_indices]

# Example usage:
model = load_model('model.pth', input_size=20, hidden_size=64)  # Use the correct input_size and hidden_size
client = MongoClient('mongodb://localhost:27017/')
db = client['Dataset']

# Fetch features for a specific song by ID or filename
features = fetch_features(db, filename="000405.mp3")

if features is not None:
    similar_songs = find_similar_songs(model, db, features)
    print("Similar songs IDs:", similar_songs)
else:
    print("Song not found.")


Skipping song 663f34827e18c8a61b05e03b because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e03f because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e046 because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e04d because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e054 because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e05a because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e05f because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e064 because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e06b because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e071 because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e077 because it doesn't have mfccs_stats
Skipping song 663f34827e18c8a61b05e07d because it doesn't have mfccs_stats
Skipping song 663f34837e18c8a61b05e082 because it doesn't have mfccs_stats
Skipping song 663f34837e1